In [10]:
import geopandas as gpd
import pandas as pd
import psycopg2

from shapely.geometry import Point

import matplotlib.pyplot as plt
import matplotlib.dates as mdates

import datetime
import matplotlib.units as munits

In [11]:
%config IPCompleter.greedy=True

In [ ]:
my_con = psycopg2.connect(database = "sk", user = "geno")
# webget = pd.read_sql("select count(*) from webget;",con = my_con)
webget = pd.read_sql("select * from webget limit 10;",con = my_con)
my_con.close()

try:
    my_con = psycopg2.connect(database = "sk", user = "geno")
except:
    print("I am unable to connect to the database.")
    
cur = my_con.cursor()
try:
    cur.execute("select unit_id, count(*) from webget group by unit_id;")
except psycopg2.OperationalError as e:
    print(e)
webget = cur.fetchall()
webget

https://imlc.me/dh-key-too-small

link incase you want to dl data to cluster.

https://postgrespro.com/list/thread-id/1222750

incase you have read blokc errors

https://sourabhbajaj.com/mac-setup/PostgreSQL/

brew services restart postgresql


# Visualizations
## Changes in service characteristics:
both spatial and in time.

1. Download
2. Upload 
3. Latency

Need to figure out calculations used in report

Changes in consumer subscriptions:
*Asking Jamie how he got usage data*
*However, it is receive and tranceive in Gb*

4. netusage

What services are being bought
Changes in consumer usage:
Is there higher demand for 
Receiving data
Transmitting
Transceiving increase due to covid is probable, but down the line, after covid, would we continue this trend of production.
If netusage is provided

5. DNS resolution as a form of understanding infrastructure

Is DNS resolution time getting shorter
Are failures less frequent
Spatial relation to DNS
Possibility of using webget information to answer this


## Work Plan
spatial data is required.
1. get spatial information for each unit.

In [12]:
#read unit-profile 2019

# Read in the SamKnows location data.
sk = pd.read_excel("UnitID-census-block-sept2019-resaved.xlsx", engine = "openpyxl")
sk.rename(columns = {"unit id" : "unit_id"}, inplace = True)

print("tract or blockgroup:", sk.geog_type.isin(["blockgroup", "tract"]).mean())

sk.query("(geog_type == 'blockgroup') | (geog_type == 'tract')", inplace = True)

# # Tract geometries from 2018 ACS.
# us4326 = gpd.read_postgis("SELECT geoid, ST_Transform(geomsimp, 4326) geom FROM census_tracts_2018;",
#                           con = cen_con, geom_col = "geom", crs = "EPSG:4326")

# # Get basic demographics from 2017 ACS.
# prof17 = pd.read_sql("SELECT geoid, log_mhi, black, total_pop FROM acsprofile5y2017;", con = cen_con)

# ## Construct rank & categories for median household income.
# prof17["mhi_rank"] = prof17.log_mhi.rank() / prof17.shape[0]
# prof17["mhi_class"] = "mid"
# prof17.loc[prof17.mhi_rank < 0.25, "mhi_class"] = "low"
# prof17.loc[prof17.mhi_rank > 0.75, "mhi_class"] = "high"

# # Read in the SamKnows location data.
# sk = pd.read_excel("sk_sept2018.xlsx", engine = "openpyxl")
# sk.rename(columns = {"unit id" : "unit_id"}, inplace = True)

# print("tract or blockgroup:", sk.geog_type.isin(["blockgroup", "tract"]).mean())

# sk.query("(geog_type == 'blockgroup') | (geog_type == 'tract')", inplace = True)

## Transform this into a GeoDataFrame since the GEOIDs are busted.
geo_sk = gpd.GeoSeries([Point(xy) for xy in sk[["longitude", "latitude"]].values], 
                       index = sk.index, crs = "EPSG:4326")

geo_sk = gpd.GeoDataFrame(data = sk, geometry = geo_sk, crs = "EPSG:4326")

# ## Merge these together.
# sk_tr18 = gpd.sjoin(geo_sk, us4326, op = "within")[["unit_id", "geoid"]]
# sk_tr18 = sk_tr18.sort_values("unit_id").reset_index(drop = True)
# sk_tr18 = sk_tr18.sort_values("unit_id")


# Check that we're not losing data by merging 2018 and 2017 profile data.
# assert(pd.merge(sk_tr18, prof17).shape[0] == sk_tr18.shape[0])

# sk_tr18 = pd.merge(sk_tr18, prof17)

tract or blockgroup: 0.9321050835892187


In [13]:
geo_sk

unit_id       geog_id   geog_type  population   latitude   longitude  \
0     27608497  180030105002  blockgroup        1256  41.107224  -85.267349   
1     27608173  191690003002  blockgroup        1146  42.053741  -93.625908   
2     27268329  180330206021  blockgroup        1518  41.341866  -85.116989   
3     26827401  360710135003  blockgroup        2321  41.352673  -74.125687   
4     26827397   36047020500       tract        2469  40.677475  -73.965704   
...        ...           ...         ...         ...        ...         ...   
2920       763  240317015062  blockgroup        2508  39.039619  -77.001938   
2921       636  480850316331  blockgroup        1563  33.067753  -96.730812   
2922       602   81230020201  blockgroup        1008  40.164696 -104.936577   
2924       566  330110195021  blockgroup        2409  42.898830  -71.680611   
2925       447   42003473100       tract        4734  40.392759  -80.050486   

                         geometry  
0      POINT (-85.26735 41.10722)  
1      POINT (-93.62591 42.05374)  
2      POINT (-85.11699 41.34187)  
3      POINT (-74.12569 41.35267)  
4      POINT (-73.96570 40.67748)  
...                           ...  
2920   POINT (-77.00194 39.03962)  
2921   POINT (-96.73081 33.06775)  
2922  POINT (-104.93658 40.16470)  
2924   POINT (-71.68061 42.89883)  
2925   POINT (-80.05049 40.39276)  

[2732 rows x 7 columns]

In [14]:
geo_sk.describe()

unit_id       geog_id    population     latitude    longitude
count  2.732000e+03  2.732000e+03   2732.000000  2732.000000  2732.000000
mean   1.128373e+07  2.411912e+11   2365.985359    38.335793   -92.297418
std    1.168950e+07  1.721175e+11   1393.912173     5.021184    16.038370
min    4.470000e+02  1.073006e+09   1001.000000    20.154507  -158.065903
25%    9.422635e+05  6.065044e+10   1416.000000    34.412055  -103.690201
50%    3.893557e+06  2.119993e+11   1901.000000    39.215118   -86.044572
75%    2.486967e+07  3.906101e+11   2790.500000    41.468485   -81.477558
max    2.760850e+07  5.602997e+11  11333.000000    48.886360   -70.065640

2. be able to plot these units onto a map

In [15]:
from mapboxgl.utils import create_color_stops, df_to_geojson
from mapboxgl.viz import CircleViz
import os
mapboxgl_token = "pk.eyJ1IjoidGhlZ3JlYXRvbmUiLCJhIjoiY2txNnN4eTBrMDdtbDMxbGY0YzRxM3o4cyJ9.hW1J2D3awtAHts2klL84gw"
print(os.getenv('MBGL_TOKEN'))
mapboxgl_token = os.getenv('MBGL_TOKEN')

pk.eyJ1IjoidGhlZ3JlYXRvbmUiLCJhIjoiY2txNnN4eTBrMDdtbDMxbGY0YzRxM3o4cyJ9.hW1J2D3awtAHts2klL84gw


In [36]:
boxes  = df_to_geojson(sk,
#    filename='boxes.geojson',
   properties=['unit_id', 'population'],
   lat='latitude', lon='longitude', precision=3)

# Generate data breaks and color stops from colorBrewer
color_breaks = [0,500,1000,1500,2000,5000,10000,15000]
color_stops = create_color_stops(color_breaks, colors='YlGnBu')

# Create the viz from the dataframe
viz = CircleViz(boxes,
                access_token=mapboxgl_token,
                height='400px',
                color_property = "population",
                color_stops = color_stops,
                center = (-95, 40),
                zoom = 3,
                below_layer = 'waterway-label'
              )
viz.show()

/home/geno/.local/lib/python3.6/site-packages/IPython/core/display.py:701: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")


## Example using python

In [26]:
import pandas as pd
import os
from mapboxgl.utils import *
from mapboxgl.viz import *

# Load data from sample csv
data_url = 'https://raw.githubusercontent.com/mapbox/mapboxgl-jupyter/master/examples/data/points.csv'
df = pd.read_csv(data_url)

# Must be a public token, starting with `pk`
token = mapboxgl_token

# Create a geojson Feature Collection export from a Pandas dataframe
points = df_to_geojson(df, 
                       properties=['Avg Medicare Payments', 'Avg Covered Charges', 'date'],
                       lat='lat', lon='lon', precision=3)

# Generate data breaks and color stops from colorBrewer
color_breaks = [0,10,100,1000,10000]
color_stops = create_color_stops(color_breaks, colors='YlGnBu')

# Create the viz from the dataframe
viz = CircleViz(points,
                access_token=token,
                height='400px',
                color_property='Avg Medicare Payments',
                color_stops=color_stops,
                label_property='Avg Medicare Payments',
                stroke_color='black',
                center=(-95, 40),
                zoom=3,
                below_layer='waterway-label')
viz.show()

## new objectives
1. cater datasets for each graph you want to produce to use with the mapboxgl js api.
2. provide link to aggregated dataset used for visualization.

### visualizations
1. boxes locations (no go ?)
2. boxes per state,city,tract (chlorepleth) (state,num)
3. boxes/population per city (inbalance in distribution)
4. number of boxes per income level (income level) (bar graph)



5. latency at median, 90,99 pt per week, per month (chlorepleth)(what's useful?:visualize latency over area) (border around urban) 3d? maybe?
6. extrapolated consumption per state,mhi 2d?
7. consumption by bandwidth overall,state,mhi 3d?

In [38]:
geo_sk

unit_id       geog_id   geog_type  population   latitude   longitude  \
0     27608497  180030105002  blockgroup        1256  41.107224  -85.267349   
1     27608173  191690003002  blockgroup        1146  42.053741  -93.625908   
2     27268329  180330206021  blockgroup        1518  41.341866  -85.116989   
3     26827401  360710135003  blockgroup        2321  41.352673  -74.125687   
4     26827397   36047020500       tract        2469  40.677475  -73.965704   
...        ...           ...         ...         ...        ...         ...   
2920       763  240317015062  blockgroup        2508  39.039619  -77.001938   
2921       636  480850316331  blockgroup        1563  33.067753  -96.730812   
2922       602   81230020201  blockgroup        1008  40.164696 -104.936577   
2924       566  330110195021  blockgroup        2409  42.898830  -71.680611   
2925       447   42003473100       tract        4734  40.392759  -80.050486   

                         geometry  
0      POINT (-85.26735 41.10722)  
1      POINT (-93.62591 42.05374)  
2      POINT (-85.11699 41.34187)  
3      POINT (-74.12569 41.35267)  
4      POINT (-73.96570 40.67748)  
...                           ...  
2920   POINT (-77.00194 39.03962)  
2921   POINT (-96.73081 33.06775)  
2922  POINT (-104.93658 40.16470)  
2924   POINT (-71.68061 42.89883)  
2925   POINT (-80.05049 40.39276)  

[2732 rows x 7 columns]

In [58]:
request=f'https://geocoding.geo.census.gov/geocoder/geographies/coordinates?x=-85.267349&y=41.107224&benchmark=4&vintage=4&format=json'
request=f'{lat}{long}'

NameError: name 'lat' is not defined

In [40]:
for i in range(geo_sk.shape[0]):
    

In [42]:
geo_sk.shape

(2732, 7)

In [43]:
geo_sk['state']

KeyError: 'state'

In [59]:
import requests
import json
request=f'https://geocoding.geo.census.gov/geocoder/geographies/coordinates?x=-87.58395178561923&y=41.799759071385395&benchmark=4&vintage=4&format=json'
request=f'https://geocoding.geo.census.gov/geocoder/geographies/coordinates?x=-85.267349&y=41.107224&benchmark=4&vintage=4&format=json'

resp = requests.get(request).json()
resp

<Response [200]>

In [64]:
print(geo_sk.loc[0])
print(resp.text)
a = (resp.json())

unit_id                               27608497
geog_id                           180030105002
geog_type                           blockgroup
population                                1256
latitude                               41.1072
longitude                             -85.2673
geometry      POINT (-85.26734924 41.10722351)
Name: 0, dtype: object
{"result":{"input":{"benchmark":{"id":"4","benchmarkName":"Public_AR_Current","benchmarkDescription":"Public Address Ranges - Current Benchmark","isDefault":false},"vintage":{"id":"4","vintageName":"Current_Current","vintageDescription":"Current Vintage - Current Benchmark","isDefault":true},"location":{"x":-85.267349,"y":41.107224}},"geographies":{"States":[{"STATENS":"00448508","GEOID":"18","CENTLAT":"+39.9059403","AREAWATER":1541613641,"STATE":"18","BASENAME":"Indiana","STUSAB":"IN","OID":2749051705222,"LSADC":"00","FUNCSTAT":"A","INTPTLAT":"+39.9013136","DIVISION":"3","NAME":"Indiana","REGION":"2","OBJECTID":49,"CENTLON":"-086.2872770",

In [61]:
a['result']['geographies']

{'States': [{'STATENS': '00448508',
   'GEOID': '18',
   'CENTLAT': '+39.9059403',
   'AREAWATER': 1541613641,
   'STATE': '18',
   'BASENAME': 'Indiana',
   'STUSAB': 'IN',
   'OID': 2749051705222,
   'LSADC': '00',
   'FUNCSTAT': 'A',
   'INTPTLAT': '+39.9013136',
   'DIVISION': '3',
   'NAME': 'Indiana',
   'REGION': '2',
   'OBJECTID': 49,
   'CENTLON': '-086.2872770',
   'AREALAND': 92788998225,
   'INTPTLON': '-086.2919129',
   'MTFCC': 'G4000'}],
 'Counties': [{'GEOID': '18003',
   'CENTLAT': '+41.0908226',
   'AREAWATER': 7053646,
   'STATE': '18',
   'BASENAME': 'Allen',
   'OID': 2759062868403,
   'LSADC': '06',
   'FUNCSTAT': 'A',
   'INTPTLAT': '+41.0919086',
   'NAME': 'Allen County',
   'OBJECTID': 137,
   'CENTLON': '-085.0665824',
   'COUNTYCC': 'H1',
   'COUNTYNS': '00450402',
   'AREALAND': 1702400299,
   'INTPTLON': '-085.0717907',
   'MTFCC': 'G4020',
   'COUNTY': '003'}],
 '2020 Census Blocks': [{'SUFFIX': '',
   'GEOID': '180030105002037',
   'CENTLAT': '+41.11369

In [65]:
_=a['result']['geographies']
state_geoid, state,county_geoid,county,census_block_2020,census_tract

NameError: name 'state_geoid' is not defined

In [ ]:
#latitude is horizontal

In [84]:
#just loop I guess
geogs_raw=[]
geo_sk["geograhies"]=""
for idx,row in geo_sk.iterrows():
#     request=f'https://geocoding.geo.census.gov/geocoder/geographies/coordinates?x=-87.58395178561923&y=41.799759071385395&benchmark=4&vintage=4&format=json'
    resp=requests.get(f"https://geocoding.geo.census.gov/geocoder/geographies/coordinates?x={row['longitude']}&y={row['latitude']}&benchmark=4&vintage=4&format=json")
    if resp.status_code==200:
        print(f'Got a resp for {idx}')
    row["geographies"]=resp.json()
    geogs_raw.append(resp.json())
    

Got a resp for 0
Got a resp for 1
Got a resp for 2
Got a resp for 3
Got a resp for 4
Got a resp for 5
Got a resp for 6
Got a resp for 7
Got a resp for 9
Got a resp for 11
Got a resp for 12
Got a resp for 14
Got a resp for 15
Got a resp for 17
Got a resp for 18
Got a resp for 19
Got a resp for 20
Got a resp for 21
Got a resp for 22
Got a resp for 23
Got a resp for 24
Got a resp for 25
Got a resp for 26
Got a resp for 27
Got a resp for 28
Got a resp for 29
Got a resp for 30
Got a resp for 31
Got a resp for 32
Got a resp for 33
Got a resp for 34
Got a resp for 35
Got a resp for 37
Got a resp for 38
Got a resp for 39
Got a resp for 40
Got a resp for 41
Got a resp for 42
Got a resp for 43
Got a resp for 44
Got a resp for 46
Got a resp for 48
Got a resp for 49
Got a resp for 50
Got a resp for 51
Got a resp for 52
Got a resp for 53
Got a resp for 54
Got a resp for 55
Got a resp for 56
Got a resp for 57
Got a resp for 58
Got a resp for 59
Got a resp for 60
Got a resp for 61
Got a resp for 62
G

Got a resp for 470
Got a resp for 471
Got a resp for 472
Got a resp for 473
Got a resp for 474
Got a resp for 475
Got a resp for 476
Got a resp for 477
Got a resp for 478
Got a resp for 480
Got a resp for 481
Got a resp for 482
Got a resp for 483
Got a resp for 485
Got a resp for 486
Got a resp for 487
Got a resp for 488
Got a resp for 491
Got a resp for 492
Got a resp for 493
Got a resp for 494
Got a resp for 495
Got a resp for 496
Got a resp for 497
Got a resp for 498
Got a resp for 499
Got a resp for 500
Got a resp for 501
Got a resp for 502
Got a resp for 503
Got a resp for 504
Got a resp for 505
Got a resp for 506
Got a resp for 507
Got a resp for 508
Got a resp for 509
Got a resp for 510
Got a resp for 511
Got a resp for 512
Got a resp for 513
Got a resp for 514
Got a resp for 515
Got a resp for 516
Got a resp for 517
Got a resp for 518
Got a resp for 519
Got a resp for 520
Got a resp for 521
Got a resp for 522
Got a resp for 524
Got a resp for 526
Got a resp for 527
Got a resp f

Got a resp for 940
Got a resp for 941
Got a resp for 942
Got a resp for 943
Got a resp for 944
Got a resp for 945
Got a resp for 946
Got a resp for 947
Got a resp for 948
Got a resp for 949
Got a resp for 950
Got a resp for 951
Got a resp for 952
Got a resp for 954
Got a resp for 955
Got a resp for 956
Got a resp for 957
Got a resp for 958
Got a resp for 959
Got a resp for 961
Got a resp for 962
Got a resp for 963
Got a resp for 964
Got a resp for 966
Got a resp for 967
Got a resp for 968
Got a resp for 969
Got a resp for 970
Got a resp for 971
Got a resp for 972
Got a resp for 973
Got a resp for 974
Got a resp for 975
Got a resp for 977
Got a resp for 978
Got a resp for 979
Got a resp for 981
Got a resp for 983
Got a resp for 984
Got a resp for 985
Got a resp for 986
Got a resp for 987
Got a resp for 988
Got a resp for 989
Got a resp for 990
Got a resp for 991
Got a resp for 992
Got a resp for 994
Got a resp for 995
Got a resp for 996
Got a resp for 997
Got a resp for 998
Got a resp f

Got a resp for 1389
Got a resp for 1390
Got a resp for 1391
Got a resp for 1392
Got a resp for 1394
Got a resp for 1395
Got a resp for 1396
Got a resp for 1397
Got a resp for 1398
Got a resp for 1399
Got a resp for 1400
Got a resp for 1401
Got a resp for 1402
Got a resp for 1403
Got a resp for 1404
Got a resp for 1405
Got a resp for 1406
Got a resp for 1407
Got a resp for 1408
Got a resp for 1409
Got a resp for 1410
Got a resp for 1411
Got a resp for 1412
Got a resp for 1413
Got a resp for 1414
Got a resp for 1415
Got a resp for 1416
Got a resp for 1417
Got a resp for 1418
Got a resp for 1419
Got a resp for 1420
Got a resp for 1421
Got a resp for 1422
Got a resp for 1423
Got a resp for 1424
Got a resp for 1425
Got a resp for 1426
Got a resp for 1427
Got a resp for 1428
Got a resp for 1429
Got a resp for 1430
Got a resp for 1431
Got a resp for 1432
Got a resp for 1433
Got a resp for 1434
Got a resp for 1435
Got a resp for 1436
Got a resp for 1437
Got a resp for 1438
Got a resp for 1439


Got a resp for 1822
Got a resp for 1823
Got a resp for 1824
Got a resp for 1825
Got a resp for 1826
Got a resp for 1827
Got a resp for 1828
Got a resp for 1829
Got a resp for 1831
Got a resp for 1832
Got a resp for 1833
Got a resp for 1834
Got a resp for 1835
Got a resp for 1836
Got a resp for 1837
Got a resp for 1838
Got a resp for 1839
Got a resp for 1840
Got a resp for 1841
Got a resp for 1842
Got a resp for 1843
Got a resp for 1844
Got a resp for 1845
Got a resp for 1846
Got a resp for 1847
Got a resp for 1848
Got a resp for 1849
Got a resp for 1850
Got a resp for 1851
Got a resp for 1852
Got a resp for 1853
Got a resp for 1854
Got a resp for 1855
Got a resp for 1857
Got a resp for 1858
Got a resp for 1859
Got a resp for 1860
Got a resp for 1861
Got a resp for 1862
Got a resp for 1863
Got a resp for 1864
Got a resp for 1865
Got a resp for 1866
Got a resp for 1867
Got a resp for 1868
Got a resp for 1869
Got a resp for 1870
Got a resp for 1871
Got a resp for 1872
Got a resp for 1873


Got a resp for 2252
Got a resp for 2253
Got a resp for 2254
Got a resp for 2255
Got a resp for 2256
Got a resp for 2257
Got a resp for 2258
Got a resp for 2259
Got a resp for 2260
Got a resp for 2261
Got a resp for 2262
Got a resp for 2263
Got a resp for 2264
Got a resp for 2265
Got a resp for 2266
Got a resp for 2267
Got a resp for 2268
Got a resp for 2269
Got a resp for 2271
Got a resp for 2272
Got a resp for 2273
Got a resp for 2274
Got a resp for 2275
Got a resp for 2276
Got a resp for 2277
Got a resp for 2278
Got a resp for 2279
Got a resp for 2280
Got a resp for 2281
Got a resp for 2282
Got a resp for 2283
Got a resp for 2285
Got a resp for 2286
Got a resp for 2287
Got a resp for 2288
Got a resp for 2289
Got a resp for 2290
Got a resp for 2291
Got a resp for 2292
Got a resp for 2293
Got a resp for 2294
Got a resp for 2295
Got a resp for 2296
Got a resp for 2297
Got a resp for 2298
Got a resp for 2299
Got a resp for 2300
Got a resp for 2301
Got a resp for 2302
Got a resp for 2303


Got a resp for 2686
Got a resp for 2687
Got a resp for 2688
Got a resp for 2689
Got a resp for 2690
Got a resp for 2691
Got a resp for 2692
Got a resp for 2693
Got a resp for 2694
Got a resp for 2695
Got a resp for 2696
Got a resp for 2697
Got a resp for 2698
Got a resp for 2699
Got a resp for 2700
Got a resp for 2701
Got a resp for 2702
Got a resp for 2703
Got a resp for 2704
Got a resp for 2705
Got a resp for 2708
Got a resp for 2709
Got a resp for 2710
Got a resp for 2711
Got a resp for 2712
Got a resp for 2713
Got a resp for 2715
Got a resp for 2716
Got a resp for 2717
Got a resp for 2718
Got a resp for 2719
Got a resp for 2720
Got a resp for 2721
Got a resp for 2722
Got a resp for 2723
Got a resp for 2725
Got a resp for 2726
Got a resp for 2728
Got a resp for 2729
Got a resp for 2730
Got a resp for 2731
Got a resp for 2732
Got a resp for 2733
Got a resp for 2734
Got a resp for 2735
Got a resp for 2736
Got a resp for 2737
Got a resp for 2738
Got a resp for 2739
Got a resp for 2740


In [85]:
geogs_raw

[{'result': {'input': {'benchmark': {'id': '4',
     'benchmarkName': 'Public_AR_Current',
     'benchmarkDescription': 'Public Address Ranges - Current Benchmark',
     'isDefault': False},
    'vintage': {'id': '4',
     'vintageName': 'Current_Current',
     'vintageDescription': 'Current Vintage - Current Benchmark',
     'isDefault': True},
    'location': {'x': -85.26734924, 'y': 41.10722351}},
   'geographies': {'States': [{'STATENS': '00448508',
      'GEOID': '18',
      'CENTLAT': '+39.9059403',
      'AREAWATER': 1541613641,
      'STATE': '18',
      'BASENAME': 'Indiana',
      'STUSAB': 'IN',
      'OID': 2749051705222,
      'LSADC': '00',
      'FUNCSTAT': 'A',
      'INTPTLAT': '+39.9013136',
      'DIVISION': '3',
      'NAME': 'Indiana',
      'REGION': '2',
      'OBJECTID': 49,
      'CENTLON': '-086.2872770',
      'AREALAND': 92788998225,
      'INTPTLON': '-086.2919129',
      'MTFCC': 'G4000'}],
    'Counties': [{'GEOID': '18003',
      'CENTLAT': '+41.0908226'

In [82]:
geo_sk.loc[0]

KeyError: 'geographies'

In [ ]:
speed_sql = """
SELECT\d
  unit_id, dtime::DATE,
  AVG(bytes_sec / 125000) speed
FROM httpgetmt 
WHERE 
  dtime::DATE != '2020-02-07' AND
  successes != 0 AND sequence < 5 AND
  (target LIKE '%mlab%' OR target LIKE '%level3%') AND 
  address != '0'
GROUP BY unit_id, dtime::DATE
ORDER BY unit_id, dtime::DATE
"""


In [ ]:
select unit_id, bytes_sec as speed from httpget where date_trunc('week',dtime)='2018-08-27 00:00:00' and unit_id=16;

In [ ]:
I think the aggregation is working. 
1. Try for a few months
2. data data visualization
3. work on flask framework
4. grab census data